In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, recall_score, precision_score, f1_score, roc_auc_score
import os

pd.options.display.max_columns = None

In [2]:
# Путь к директории с данными

data_dir = '/home/common/emergency_datahack/data_processed/track_1_package/track_1/'
os.listdir(data_dir)

['meteo_coord.csv',
 'meteo_1day.csv',
 'reference_water_codes.csv',
 'meteo_1month.csv',
 'hydro_coord.csv',
 'reference_horiz_visib.csv',
 'meteo_3hours.csv',
 'ice_saw.csv',
 'train.csv',
 'test.csv',
 'hydro_1day.csv']

In [3]:
# Загрузим всё
main_df = pd.read_csv(data_dir + 'train.csv')

# Метео
mc = pd.read_csv(data_dir + 'meteo_coord.csv')
mld = pd.read_csv(data_dir + 'meteo_1day.csv')
mlm = pd.read_csv(data_dir + 'meteo_1month.csv')
rhv = pd.read_csv(data_dir + 'reference_horiz_visib.csv')

# Гидро
hc = pd.read_csv(data_dir + 'hydro_coord.csv')
hld = pd.read_csv(data_dir + 'hydro_1day.csv',
                   parse_dates=['date'])
rwc = pd.read_csv(data_dir + 'reference_water_codes.csv')

In [4]:
# Подтянем ближайшую к гидростанции метеостанцию

from geopy.distance import geodesic
import re

def merge_coord(df):
    df['lat_long'] = df[['lat', 'lon']].apply(tuple, axis=1)
    return df

def stat_km(point, stat_list):
    stations_list=stat_list
    lst=[]
    if pd.isnull(point):
        lst.append(np.nan)
    else:
        for i in stations_list['lat_long']:
            x=geodesic(point, i).km
            lst.append(x)
            stations_list['dist']=pd.DataFrame(lst)
        y=stations_list['station_id'][stations_list['dist'] == stations_list['dist'].min()]
        y=y.to_string()
        y=re.sub("^[0-9]+", "", y)
        y=re.sub(" +", "", y)
        return int(y)

hc = merge_coord(hc)
mc = merge_coord(mc)
hc['closest_hydro'] = mc.lat_long.apply(lambda x: stat_km(x, mc))

In [5]:
mld = mld.merge(hc[['station_id', 'closest_hydro']], left_on=['station_id'], 
                right_on='closest_hydro', how='right')
mld.drop(['station_id_x', 'closest_hydro', 'date'], axis=1, inplace=True)
mld.rename({'station_id_y': 'station_id'}, axis=1, inplace=True)

### Разделим годы на train и test сбалансированно по суммарной продолжительности заторных событий

In [6]:
# Суммарное количество заторов в году
jams_by_year = main_df.groupby('year').sum()['ice_jam'].to_frame().reset_index()
jams_by_year['ice_jam'].describe()

count    26.000000
mean      5.307692
std       3.792300
min       0.000000
25%       3.000000
50%       5.000000
75%       8.000000
max      16.000000
Name: ice_jam, dtype: float64

In [7]:
# Разделим на бины по квартилям
bins = [-1, 3, 5, 8, 16]
jams_by_year['ice_jam_bins'] = pd.cut(jams_by_year['ice_jam'], bins)
X_length = jams_by_year[['year', 'ice_jam']]
y_length = jams_by_year['ice_jam_bins']
y_length.value_counts()

(-1, 3]    9
(3, 5]     7
(5, 8]     6
(8, 16]    4
Name: ice_jam_bins, dtype: int64

In [8]:
# Разделим годы на трейн и тест
X_train, X_test, y_train, y_test = train_test_split(X_length, 
                                                    y_length, 
                                                    test_size=0.3,  
                                                    stratify=y_length, 
                                                    random_state=42)

### Соберем фичи из гидроданных

<div class="alert alert-block alert-warning">
Мы не можем использовать данные из будущего: всё, что происходит после заторного периода, относится уже к следующему году.
</div>

In [9]:
# Внесем не темпоральные данные
main_df = pd.merge(main_df, hc[['station_id', 
                                'distance_from_source', 
                                'drainage_area', 
                                'z_null']], on='station_id', how='left')

# Возьмем также данные из ежедневных наблюдений
hld = pd.read_csv(data_dir + 'hydro_1day.csv',
                   parse_dates=['date'])
hld.head(1)

year  station_id  month  day       date  stage_avg  stage_min  stage_max  \
0  2000        3019      1    1 2000-01-01       74.0       74.0       74.0   

   temp water_code  ice_thickness  snow_height  place  discharge  
0   NaN         46            NaN          NaN    NaN        NaN

In [10]:
hld['station_id'] = hld.station_id.astype(int)
mld['station_id'] = mld['station_id'].astype(int)

In [11]:
hld.head()

year  station_id  month  day       date  stage_avg  stage_min  stage_max  \
0  2000        3019      1    1 2000-01-01       74.0       74.0       74.0   
1  2000        3019      1    2 2000-01-02       70.0       70.0       70.0   
2  2000        3019      1    3 2000-01-03       67.0       67.0       67.0   
3  2000        3019      1    4 2000-01-04       64.0       64.0       64.0   
4  2000        3019      1    5 2000-01-05       60.0       60.0       60.0   

   temp water_code  ice_thickness  snow_height  place  discharge  
0   NaN         46            NaN          NaN    NaN        NaN  
1   NaN         46            NaN          NaN    NaN        NaN  
2   NaN         46            NaN          NaN    NaN        NaN  
3   NaN         46            NaN          NaN    NaN        NaN  
4   NaN         46            NaN          NaN    NaN        NaN

In [12]:
mld.head()

year  month  day  route_type  snow_coverage_near_station  \
0  1985      1    1         NaN                         NaN   
1  1985      1    2         NaN                         NaN   
2  1985      1    3         NaN                         NaN   
3  1985      1    4         NaN                         NaN   
4  1985      1    5         NaN                         NaN   

   snow_coverage_route  ice_crust_route  snow_height_aver  snow_height_max  \
0                  NaN              NaN               NaN              NaN   
1                  NaN              NaN               NaN              NaN   
2                  NaN              NaN               NaN              NaN   
3                  NaN              NaN               NaN              NaN   
4                  NaN              NaN               NaN              NaN   

   snow_height_min  snow_density_aver  ice_crust_aver  \
0              NaN                NaN             NaN   
1              NaN                NaN             NaN   
2              NaN                NaN             NaN   
3              NaN                NaN             NaN   
4              NaN                NaN             NaN   

   snow_saturated_thickness  water_thickness  water_in_snow  water_total  \
0                       NaN              NaN            NaN          NaN   
1                       NaN              NaN            NaN          NaN   
2                       NaN              NaN            NaN          NaN   
3                       NaN              NaN            NaN          NaN   
4                       NaN              NaN            NaN          NaN   

   snow_coverage_charact  snow_charact  snow_height  snow_coverage_station  \
0                    NaN           NaN         32.0                   10.0   
1                    NaN           NaN         32.0                   10.0   
2                    NaN           NaN         32.0                   10.0   
3                    NaN           NaN         32.0                   10.0   
4                    NaN           NaN         32.0                   10.0   

   snow_height_q1  snow_height_q2  snow_height_q3  temperature_20cm  \
0             0.0             0.0             0.0               NaN   
1             0.0             0.0             0.0               NaN   
2             0.0             0.0             0.0               NaN   
3             0.0             0.0             0.0               NaN   
4             0.0             0.0             0.0               NaN   

   temperature_20cm_qual  temperature_40cm  temperature_40cm_qual  \
0                    NaN               NaN                    NaN   
1                    NaN               NaN                    NaN   
2                    NaN               NaN                    NaN   
3                    NaN               NaN                    NaN   
4                    NaN               NaN                    NaN   

   temperature_80cm  temperature_80cm_qual  temperature_120cm  \
0               NaN                    NaN                NaN   
1               NaN                    NaN                NaN   
2               NaN                    NaN                NaN   
3               NaN                    NaN                NaN   
4               NaN                    NaN                NaN   

   temperature_120cm_qual  temperature_160cm  temperature_160cm_qual  \
0                     NaN                NaN                     NaN   
1                     NaN                NaN                     NaN   
2                     NaN                NaN                     NaN   
3                     NaN                NaN                     NaN   
4                     NaN                NaN                     NaN   

   temperature_240cm  temperature_240cm_qual  temperature_320cm  \
0                NaN                     NaN                NaN   
1                NaN                     NaN                NaN   
2                Na

In [13]:
hld = hld.merge(mld, on=['station_id', 'year', 'month', 'day'], how='inner')
hld = hld.fillna(0)
hld.head()

year  station_id  month  day       date  stage_avg  stage_min  stage_max  \
0  2000        3019      1    1 2000-01-01       74.0       74.0       74.0   
1  2000        3019      1    2 2000-01-02       70.0       70.0       70.0   
2  2000        3019      1    3 2000-01-03       67.0       67.0       67.0   
3  2000        3019      1    4 2000-01-04       64.0       64.0       64.0   
4  2000        3019      1    5 2000-01-05       60.0       60.0       60.0   

   temp water_code  ice_thickness  snow_height_x  place  discharge  \
0   0.0         46            0.0            0.0    0.0        0.0   
1   0.0         46            0.0            0.0    0.0        0.0   
2   0.0         46            0.0            0.0    0.0        0.0   
3   0.0         46            0.0            0.0    0.0        0.0   
4   0.0         46            0.0            0.0    0.0        0.0   

   route_type  snow_coverage_near_station  snow_coverage_route  \
0         0.0                         0.0                  0.0   
1         0.0                         0.0                  0.0   
2         0.0                         0.0                  0.0   
3         0.0                         0.0                  0.0   
4         0.0                         0.0                  0.0   

   ice_crust_route  snow_height_aver  snow_height_max  snow_height_min  \
0              0.0               0.0              0.0              0.0   
1              0.0               0.0              0.0              0.0   
2              0.0               0.0              0.0              0.0   
3              0.0               0.0              0.0              0.0   
4              0.0               0.0              0.0              0.0   

   snow_density_aver  ice_crust_aver  snow_saturated_thickness  \
0                0.0             0.0                       0.0   
1                0.0             0.0                       0.0   
2                0.0             0.0                       0.0   
3                0.0             0.0                       0.0   
4                0.0             0.0                       0.0   

   water_thickness  water_in_snow  water_total  snow_coverage_charact  \
0              0.0            0.0          0.0                    0.0   
1              0.0            0.0          0.0                    0.0   
2              0.0            0.0          0.0                    0.0   
3              0.0            0.0          0.0                    0.0   
4              0.0            0.0          0.0                    0.0   

   snow_charact  snow_height_y  snow_coverage_station  snow_height_q1  \
0           0.0           44.0                   10.0             0.0   
1           0.0           44.0                   10.0             0.0   
2           0.0           45.0                   10.0             0.0   
3           0.0           45.0                   10.0             0.0   
4           0.0           46.0                   10.0             0.0   

   snow_height_q2  snow_height_q3  temperature_20cm  temperature_20cm_qual  \
0             0.0             0.0               0.0                    0.0   
1             0.0             0.0               0.0                    0.0   
2             0.0             0.0               0.0                    0.0   
3             0.0             0.0               0.0                    0.0   
4             0.0             0.0               0.0                    0.0   

   temperature_40cm  temperature_40cm_qual  temperature_80cm  \
0               0.0                    0.0               0.0   
1               0.0                    0.0               0.0   
2               0.0                    0.0               0.0   
3               0.0                    0.0               0.0   
4               0.0                    0.0               0.0   

   temperature_80cm_qual  temperature_120cm  temperature_120cm_qual  \
0                    0.0                0.0                     0

### Скорректируем год, в который доступно наблюдение

In [14]:
# Определим для наблюдения год, в который оно доступно

# Маска-окно между заторным периодом и концом года
def after_jam_window(row, local=False):
    if local:
        month = row.month_local
        day = row.date_local.day
    else:
        month = row.month
        day = row.date.day
    return (((month == 6) and (day > 3))
            or (month in [7, 8, 9, 10, 11, 12]))

# Год относительно бизнес-логики
def target_year(row, local=False):
    if local:
        year = row.year_local
    else:
        year = row.year
    if after_jam_window(row):
        return year + 1
    else:
        return year
    
hld['target_year'] = hld.apply(target_year, axis=1)

# Календарный год и день больше не нужны
hld.drop(columns=['year', 'date', 'day'], axis=1, inplace=True)

In [15]:
# Гидро – сделаем ресэмплинг по месяцу

index = ['station_id', 'month', 'target_year']

hld_mean = hld.groupby(index).mean().add_prefix('mean_').reset_index()
hld_max = hld.groupby(index).max().add_prefix('max_').reset_index()
hld_min = hld.groupby(index).min().add_prefix('min_').reset_index()
hld_std = hld.groupby(index).std().add_prefix('std_').reset_index()
data_frames = [hld_mean, hld_max, hld_min, hld_std]

hydro_monthly = pd.concat(data_frames, axis=1)
hydro_monthly = hydro_monthly.loc[:,~hydro_monthly.columns.duplicated()]
hydro_monthly.sort_values(index).head()

station_id  month  target_year  mean_stage_avg  mean_stage_min  \
0        3019      1         1985      -25.709677      -25.709677   
1        3019      1         1986       56.322581       56.000000   
2        3019      1         1987        9.032258        8.516129   
3        3019      1         1988       28.806452       28.516129   
4        3019      1         1989       82.741935       82.225806   

   mean_stage_max  mean_temp  mean_ice_thickness  mean_snow_height_x  \
0      -25.580645        0.0           10.612903            6.709677   
1       56.451613        0.0            8.516129            5.774194   
2        9.161290        0.0            9.322581            3.580645   
3       28.806452        0.0            9.096774            5.290323   
4       82.774194        0.0            9.225806            7.774194   

   mean_place  mean_discharge  mean_route_type  \
0    0.193548             0.0              0.0   
1    0.193548             0.0              0.0   
2    0.193548             0.0              0.0   
3    0.193548             0.0              0.0   
4    0.193548             0.0              0.0   

   mean_snow_coverage_near_station  mean_snow_coverage_route  \
0                              0.0                       0.0   
1                              0.0                       0.0   
2                              0.0                       0.0   
3                              0.0                       0.0   
4                              0.0                       0.0   

   mean_ice_crust_route  mean_snow_height_aver  mean_snow_height_max  \
0                   0.0                    0.0                   0.0   
1                   0.0                    0.0                   0.0   
2                   0.0                    0.0                   0.0   
3                   0.0                    0.0                   0.0   
4                   0.0                    0.0                   0.0   

   mean_snow_height_min  mean_snow_density_aver  mean_ice_crust_aver  \
0                   0.0                     0.0                  0.0   
1                   0.0                     0.0                  0.0   
2                   0.0                     0.0                  0.0   
3                   0.0                     0.0                  0.0   
4                   0.0                     0.0                  0.0   

   mean_snow_saturated_thickness  mean_water_thickness  mean_water_in_snow  \
0                            0.0                   0.0                 0.0   
1                            0.0                   0.0                 0.0   
2                            0.0                   0.0                 0.0   
3                            0.0                   0.0                 0.0   
4                            0.0                   0.0                 0.0   

   mean_water_total  mean_snow_coverage_charact  mean_snow_charact  \
0               0.0                         0.0                0.0   
1               0.0                         0.0                0.0   
2               0.0                         0.0                0.0   
3               0.0                         0.0                0.0   
4               0.0                         0.0                0.0   

   mean_snow_height_y  mean_snow_coverage_station  mean_snow_height_q1  \
0           33.064516                        10.0                  0.0   
1           32.129032                        10.0                  0.0   
2           25.419355                        10.0                  0.0   
3           37.322581                        10.0                  0.0   
4           35.225806                        10.0                  0.0   

   mean_snow_height_q2  mean_snow_height_q3  mean_temperature_20cm  \
0                  0.0                  0.0                    0.0   
1                  0.0                  0.0                    0.0   
2                  0.0                  0.0               

In [16]:
def make_features(df):
    station, target_year = df.name
    result = pd.DataFrame()
    for month, mdf in df.groupby('month'):
        m_feats = mdf[df.columns[4:]].add_prefix(str(month) + '_').reset_index(drop=True)
        result = pd.concat([result, m_feats], axis=1)
    return result.reset_index(drop=True)
        
hydro_features = hydro_monthly.groupby(['station_id', 'target_year']).apply(make_features)
hydro_features = hydro_features.reset_index(level=2, drop=True).reset_index()
hydro_features.dropna(how='all', axis=1, inplace=True)
hydro_features

station_id  target_year  1_mean_stage_min  1_mean_stage_max  1_mean_temp  \
0          3019         1985        -25.709677        -25.580645          0.0   
1          3019         1986         56.000000         56.451613          0.0   
2          3019         1987          8.516129          9.161290          0.0   
3          3019         1988         28.516129         28.806452          0.0   
4          3019         1989         82.225806         82.774194          0.0   
..          ...          ...               ...               ...          ...   
915        3555         2016        248.225806        248.225806          0.0   
916        3555         2017        282.000000        282.000000          0.0   
917        3555         2018        251.354839        251.354839          0.0   
918        3555         2019        270.967742        270.967742          0.0   
919        3555         2020               NaN               NaN          NaN   

     1_mean_ice_thickness  1_mean_snow_height_x  1_mean_place  \
0               10.612903              6.709677      0.193548   
1                8.516129              5.774194      0.193548   
2                9.322581              3.580645      0.193548   
3                9.096774              5.290323      0.193548   
4                9.225806              7.774194      0.193548   
..                    ...                   ...           ...   
915              5.709677              4.548387      0.193548   
916              4.580645              3.806452      0.193548   
917              3.967742              3.806452      0.096774   
918              3.612903              2.419355      0.096774   
919                   NaN                   NaN           NaN   

     1_mean_discharge  1_mean_route_type  1_mean_snow_coverage_near_station  \
0                 0.0           0.000000                                0.0   
1                 0.0           0.000000                                0.0   
2                 0.0           0.000000                                0.0   
3                 0.0           0.000000                                0.0   
4                 0.0           0.000000                                0.0   
..                ...                ...                                ...   
915               0.0           0.193548                                0.0   
916               0.0           0.193548                                0.0   
917               0.0           0.193548                                0.0   
918               0.0           0.193548                                0.0   
919               NaN                NaN                                NaN   

     1_mean_snow_coverage_route  1_mean_ice_crust_route  \
0                      0.000000                     0.0   
1                      0.000000                     0.0   
2                      0.000000                     0.0   
3                      0.000000                     0.0   
4                      0.000000                     0.0   
..                          ...                     ...   
915                    0.967742                     0.0   
916                    0.967742                     0.0   
917                    0.967742                     0.0   
918                    0.967742                     0.0   
919                         NaN                     NaN   

     1_mean_snow_height_aver  1_mean_snow_height_max  1_mean_snow_height_min  \
0                   0.000000                0.000000                0.000000   
1                   0.000000                0.000000                0.000000   
2                   0.000000                0.000000                0.000000   
3                   0.000000                0.000000                0.000000   
4                   0.000000                0.000000                0.000000   
..                       ...                     ...                     ...   
915                 3.741935     

### Соберем фичи в основной датасет

<div class="alert alert-block alert-success">
Важно: merge делаем по target_year.
</div>

In [17]:
main_df = pd.merge(main_df, hydro_features, left_on=['year', 'station_id'],
                   right_on=['target_year', 'station_id'],
                   how='left')
cols = main_df.columns.to_list()
main_df = main_df[cols[:3] + [cols[7]] + cols[5:7] + cols[8:] + [cols[3]]]
main_df.dropna(how='any',inplace=True)
main_df.head(2)

year  station_id  day  target_year  drainage_area  z_null  \
0  2000        3019    1       2000.0          92200  249.38   
1  2000        3019    2       2000.0          92200  249.38   

   1_mean_stage_min  1_mean_stage_max  1_mean_temp  1_mean_ice_thickness  \
0         43.322581         43.322581          0.0              6.032258   
1         43.322581         43.322581          0.0              6.032258   

   1_mean_snow_height_x  1_mean_place  1_mean_discharge  1_mean_route_type  \
0              2.709677      0.096774               0.0                0.0   
1              2.709677      0.096774               0.0                0.0   

   1_mean_snow_coverage_near_station  1_mean_snow_coverage_route  \
0                                0.0                         0.0   
1                                0.0                         0.0   

   1_mean_ice_crust_route  1_mean_snow_height_aver  1_mean_snow_height_max  \
0                     0.0                      0.0                     0.0   
1                     0.0                      0.0                     0.0   

   1_mean_snow_height_min  1_mean_snow_density_aver  1_mean_ice_crust_aver  \
0                     0.0                       0.0                    0.0   
1                     0.0                       0.0                    0.0   

   1_mean_snow_saturated_thickness  1_mean_water_thickness  \
0                              0.0                     0.0   
1                              0.0                     0.0   

   1_mean_water_in_snow  1_mean_water_total  1_mean_snow_coverage_charact  \
0                   0.0                 0.0                           0.0   
1                   0.0                 0.0                           0.0   

   1_mean_snow_charact  1_mean_snow_height_y  1_mean_snow_coverage_station  \
0                  0.0             46.645161                          10.0   
1                  0.0             46.645161                          10.0   

   1_mean_snow_height_q1  1_mean_snow_height_q2  1_mean_snow_height_q3  \
0                    0.0                    0.0                    0.0   
1                    0.0                    0.0                    0.0   

   1_mean_temperature_20cm  1_mean_temperature_20cm_qual  \
0                      0.0                           0.0   
1                      0.0                           0.0   

   1_mean_temperature_40cm  1_mean_temperature_40cm_qual  \
0                      0.0                           0.0   
1                      0.0                           0.0   

   1_mean_temperature_80cm  1_mean_temperature_80cm_qual  \
0                      0.0                           0.0   
1                      0.0                           0.0   

   1_mean_temperature_120cm  1_mean_temperature_120cm_qual  \
0                       0.0                            0.0   
1                       0.0                            0.0   

   1_mean_temperature_160cm  1_mean_temperature_160cm_qual  \
0                       0.0                            0.0   
1                       0.0                            0.0   

   1_mean_temperature_240cm  1_mean_temperature_240cm_qual  \
0                       0.0                            0.0   
1                       0.0                            0.0   

   1_mean_temperature_320cm  1_mean_temperature_320cm_qual  \
0                       0.0                            0.0   
1                       0.0                            0.0   

   1_mean_temperature_ks_5cm  1_mean_temperature_ks_5cm_qual  \
0                        0.0                             0.0   
1                        0.0                             0.0   

   1_mean_temperature_ks_10cm  1_mean_temperature_ks_10cm_qual  \
0                         0.0                              0.0   
1                         0.0                              0.0   

   1_mean_temperature_ks_15cm  1_mean_temperature_ks_15cm_qual  \
0                         0.0                

### Нормируем фичи

In [18]:
from sklearn.preprocessing import StandardScaler

ids, data, target = main_df[main_df.columns[:4]], main_df[main_df.columns[4:-1]], main_df[main_df.columns[-1]]

scaler = StandardScaler()
scaler.fit(data)
transformed_data = scaler.transform(data)
norm_df = pd.concat([ids, pd.DataFrame(transformed_data, columns = main_df.columns[4:-1]), target], axis=1)
norm_df

year  station_id   day  target_year  drainage_area    z_null  \
0      2000.0      3019.0   1.0       2000.0      -1.250208  2.027005   
1      2000.0      3019.0   2.0       2000.0      -1.250208  2.027005   
2      2000.0      3019.0   3.0       2000.0      -1.250208  2.027005   
3      2000.0      3019.0   4.0       2000.0      -1.250208  2.027005   
4      2000.0      3019.0   5.0       2000.0      -1.250208  2.027005   
...       ...         ...   ...          ...            ...       ...   
11272  1999.0      3027.0  39.0       1999.0            NaN       NaN   
11273  1999.0      3027.0  40.0       1999.0            NaN       NaN   
11274  1999.0      3027.0  41.0       1999.0            NaN       NaN   
11275  1999.0      3027.0  42.0       1999.0            NaN       NaN   
11276  1999.0      3027.0  43.0       1999.0            NaN       NaN   

       1_mean_stage_min  1_mean_stage_max  1_mean_temp  1_mean_ice_thickness  \
0             -0.273503         -0.273754          0.0             -0.851962   
1             -0.273503         -0.273754          0.0             -0.851962   
2             -0.273503         -0.273754          0.0             -0.851962   
3             -0.273503         -0.273754          0.0             -0.851962   
4             -0.273503         -0.273754          0.0             -0.851962   
...                 ...               ...          ...                   ...   
11272               NaN               NaN          NaN                   NaN   
11273               NaN               NaN          NaN                   NaN   
11274               NaN               NaN          NaN                   NaN   
11275               NaN               NaN          NaN                   NaN   
11276               NaN               NaN          NaN                   NaN   

       1_mean_snow_height_x  1_mean_place  1_mean_discharge  \
0                  0.208741     -0.296448         -0.337384   
1                  0.208741     -0.296448         -0.337384   
2                  0.208741     -0.296448         -0.337384   
3                  0.208741     -0.296448         -0.337384   
4                  0.208741     -0.296448         -0.337384   
...                     ...           ...               ...   
11272                   NaN           NaN               NaN   
11273                   NaN           NaN               NaN   
11274                   NaN           NaN               NaN   
11275                   NaN           NaN               NaN   
11276                   NaN           NaN               NaN   

       1_mean_route_type  1_mean_snow_coverage_near_station  \
0               -1.25214                           -0.33743   
1               -1.25214                           -0.33743   
2               -1.25214                           -0.33743   
3               -1.25214                           -0.33743   
4               -1.25214                           -0.33743   
...                  ...                                ...   
11272                NaN                                NaN   
11273                NaN                                NaN   
11274                NaN                                NaN   
11275                NaN                                NaN   
11276                NaN                                NaN   

       1_mean_snow_coverage_route  1_mean_ice_crust_route  \
0                       -1.231207                     0.0   
1                       -1.231207                     0.0   
2                       -1.231207                     0.0   
3                       -1.231207                     0.0   
4                       -1.231207                     0.0   
...                           ...                     ...   
11272                         NaN                     NaN   
11273                         NaN                     NaN   
11274                         NaN                     NaN   
11275                         NaN              

In [19]:
# Разделим на трейн и тест исходя из target_year

test = norm_df[~norm_df.target_year.isin(X_train.year.to_list())].reset_index(drop=True).dropna()
train = norm_df[norm_df.target_year.isin(X_train.year.to_list())].reset_index(drop=True).dropna()

# target_year больше не нужна

test.drop(columns=['target_year'], inplace=True)
train.drop(columns=['target_year'], inplace=True)

In [20]:
# Поделим данные на предикторы и таргет

X_train, y_train = train.iloc[:, :-1], train.ice_jam
X_test, y_test = test.iloc[:, :-1], test.ice_jam

In [21]:
X_train

year  station_id   day  drainage_area    z_null  1_mean_stage_min  \
0     2000.0      3019.0   1.0      -1.250208  2.027005         -0.273503   
1     2000.0      3019.0   2.0      -1.250208  2.027005         -0.273503   
2     2000.0      3019.0   3.0      -1.250208  2.027005         -0.273503   
3     2000.0      3019.0   4.0      -1.250208  2.027005         -0.273503   
4     2000.0      3019.0   5.0      -1.250208  2.027005         -0.273503   
...      ...         ...   ...            ...       ...               ...   
6111  1992.0      3035.0  40.0      -1.004878  0.712382         -0.094826   
6112  1992.0      3035.0  41.0      -1.004878  0.712382         -0.094826   
6113  1992.0      3035.0  42.0      -1.004878  0.712382         -0.094826   
6114  1992.0      3035.0  43.0      -1.004878  0.712382         -0.094826   
6115  1992.0      3035.0  44.0      -1.004878  0.712382         -0.094826   

      1_mean_stage_max  1_mean_temp  1_mean_ice_thickness  \
0            -0.273754          0.0             -0.851962   
1            -0.273754          0.0             -0.851962   
2            -0.273754          0.0             -0.851962   
3            -0.273754          0.0             -0.851962   
4            -0.273754          0.0             -0.851962   
...                ...          ...                   ...   
6111         -0.095067          0.0             -1.246775   
6112         -0.095067          0.0             -1.246775   
6113         -0.095067          0.0             -1.246775   
6114         -0.095067          0.0             -1.246775   
6115         -0.095067          0.0             -1.246775   

      1_mean_snow_height_x  1_mean_place  1_mean_discharge  1_mean_route_type  \
0                 0.208741     -0.296448         -0.337384          -1.252140   
1                 0.208741     -0.296448         -0.337384          -1.252140   
2                 0.208741     -0.296448         -0.337384          -1.252140   
3                 0.208741     -0.296448         -0.337384          -1.252140   
4                 0.208741     -0.296448         -0.337384          -1.252140   
...                    ...           ...               ...                ...   
6111             -0.686197     -0.296448         -0.337384           1.068065   
6112             -0.686197     -0.296448         -0.337384           1.068065   
6113             -0.686197     -0.296448         -0.337384           1.068065   
6114             -0.686197     -0.296448         -0.337384           1.068065   
6115             -0.686197     -0.296448         -0.337384           1.068065   

      1_mean_snow_coverage_near_station  1_mean_snow_coverage_route  \
0                              -0.33743                   -1.231207   
1                              -0.33743                   -1.231207   
2                              -0.33743                   -1.231207   
3                              -0.33743                   -1.231207   
4                              -0.33743                   -1.231207   
...                                 ...                         ...   
6111                           -0.33743                    0.605226   
6112                           -0.33743                    0.605226   
6113                           -0.33743                    0.605226   
6114                           -0.33743                    0.605226   
6115                           -0.33743                    0.605226   

      1_mean_ice_crust_route  1_mean_snow_height_aver  1_mean_snow_height_max  \
0                        0.0                -1.035231               -1.042948   
1                        0.0                -1.035231               -1.042948   
2                        0.0                -1.035231               -1.042948   
3                        0.0                -1.035231               -1.042948   
4                        0.0                -1.035231               -1.042948   
...                      ...          

### Обучим простой классификатор

In [22]:
from sklearn.svm import SVC
from sklearn.feature_selection import RFE
from sklearn.linear_model import LogisticRegression
from sklearn.decomposition import PCA
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline

In [23]:
pca = PCA()
parameters = {'pca__n_components': list(range(400,500,50)), 'svc__kernel':('linear', 'rbf'), 'svc__C':[1,10]}
clf = Pipeline([('pca', pca), ('svc', SVC(class_weight='balanced'))])
GS = GridSearchCV(clf, parameters, scoring='f1_macro')
GS.fit(X_train, y_train)
print(GS.cv_results_)
print(GS.best_params_)

{'mean_fit_time': array([3.59678826, 3.2868701 , 6.18434196, 2.6810854 , 4.11019697,
       3.90990334, 6.89873781, 3.13560147]), 'std_fit_time': array([0.38545981, 0.24955519, 0.82937734, 0.27485547, 0.43437022,
       0.2363589 , 0.71815498, 0.12917487]), 'mean_score_time': array([0.24984441, 0.63606362, 0.2563148 , 0.38110032, 0.2804028 ,
       0.7145546 , 0.27530413, 0.40618429]), 'std_score_time': array([0.02291084, 0.08328799, 0.02050124, 0.04650943, 0.02625095,
       0.15608724, 0.02696769, 0.04371634]), 'param_pca__n_components': masked_array(data=[400, 400, 400, 400, 450, 450, 450, 450],
             mask=[False, False, False, False, False, False, False, False],
       fill_value='?',
            dtype=object), 'param_svc__C': masked_array(data=[1, 1, 10, 10, 1, 1, 10, 10],
             mask=[False, False, False, False, False, False, False, False],
       fill_value='?',
            dtype=object), 'param_svc__kernel': masked_array(data=['linear', 'rbf', 'linear', 'rbf', 'lin

In [24]:
prediction = GS.predict(X_test)
recall_score(y_test, prediction), \
    precision_score(y_test, prediction), f1_score(y_test, prediction)

(0.42857142857142855, 0.0759493670886076, 0.12903225806451613)

In [25]:
test = pd.read_csv(data_dir + 'test.csv')
test_real = pd.read_csv(data_dir + '../test_SECRET.csv')

In [26]:
test_real.head()

year  station_id  day  ice_jam
0  2001        3019    0      0.0
1  2001        3019    1      0.0
2  2001        3019    2      0.0
3  2001        3019    3      0.0
4  2001        3019    4      0.0

In [27]:
test_X = pd.merge(test_real, hc[['station_id', 
                                'distance_from_source', 
                                'drainage_area', 
                                'z_null']], on='station_id', how='left')

In [28]:
'year' in hydro_features.columns

False

In [29]:
test_X = pd.merge(test_X, hydro_features, left_on=['year', 'station_id'],
                   right_on=['target_year', 'station_id'],
                   how='left')
cols = test_X.columns.to_list()
test_X = test_X[cols[:3] + [cols[7]] + cols[5:7] + cols[8:] + [cols[3]]]

In [30]:
ids, data, target = test_X[test_X.columns[:4]], test_X[test_X.columns[4:-1]], test_X[test_X.columns[-1]]

transformed_data = scaler.transform(data)
test_X = pd.concat([ids, pd.DataFrame(transformed_data, columns = main_df.columns[4:-1]), target], axis=1)
X_test_real, y_test_real = test_X.iloc[:, :-1], test_X.ice_jam

In [31]:
X_test_real.drop('target_year',inplace=True,axis=1)
X_test_real = X_test_real.fillna(0)

In [32]:
#X_test_real_reduced = selector.transform(X_test_real)
prediction =  GS.predict(X_test_real)
accuracy_score(y_test_real, prediction), recall_score(y_test_real, prediction), \
    precision_score(y_test_real, prediction), f1_score(y_test_real, prediction)

(0.8850486431131592,
 0.3103448275862069,
 0.04215456674473068,
 0.07422680412371134)